In [87]:
#from utils import *

import numpy as np
import torch
import matplotlib.pyplot as plt
import pandas as pd
import re
from os import mkdir
from os.path import join, isfile, isdir, exists
import bcolz
import pickle 
import emoji
import torch.nn as nn
import torch.nn.functional as F
from torch.utils.data import DataLoader, Dataset
import torch.optim as optim
from pattern.en import spelling
from tqdm import tqdm
import ast

In [7]:
%matplotlib inline
%load_ext autoreload
%autoreload

In [110]:
 haha = spelling.suggest('poney')
text = ['', '   ', 'yolo']
text = [text[i] for i in range(len(text)) if text[i] != '']
text

['   ', 'yolo']

In [62]:
d = {'lol' : 'xD' , 'hhehehe' : 'funny'}
t = ['I','am' ,'very' ,'lol', 'hhehehe' ,'extremely', 'funny']
%timeit t_ = [d.get(k,k) for k in t]
t_

1 µs ± 36.1 ns per loop (mean ± std. dev. of 7 runs, 1000000 loops each)


['I', 'am', 'very', 'xD', 'funny', 'extremely', 'funny']

## Word Embedings : GloVe
This Class Loads the GloVe Embeding, processes it, and create a word embedding given the DataLoader.

In [64]:
class GloVe_embedding(object):
    def __init__(self,dim_vect = 25 ):
        ########## VARIABLES ##########
        self.dim_vect = dim_vect

        # Defining variables for GloVe: 
        self.words = []
        self.word2idx = {}
        self.glove_dict = {}
        
        ########## LOADING GLOVE DATA ##########
        
        # Defining path for GloVe Data : 
        self.path = join('..','data','glove') # Path of glove
        self.path_glove = join(self.path,'glove.twitter.27B.'+str(dim_vect))
        if not(isdir(self.path_glove)):
            mkdir(self.path_glove)
        self.path_vec_original = join(self.path,'glove.twitter.27B.'+str(dim_vect)+'d.txt') # Path of glove original vectors
        self.path_vec_save = join(self.path_glove,'glove.twitter.27B.'+str(dim_vect)+'d.vectors.dat')  # Path of glove saved vectors
        self.path_words = join(self.path_glove,'glove.twitter.27B.'+str(dim_vect)+'d.words.pkl')
        self.path_word2idx = join(self.path_glove,'glove.twitter.27B.'+str(dim_vect)+'d.word2idx.pkl')
                
        if not(isdir(self.path_vec_save) and isfile(self.path_words) and isfile(self.path_word2idx)) : 
            # If files are allready processed, just load them
            print('---- Processing the GloVe files : ',end='')
            self.process_GloVe()
            print('Done')
            
        # Load the wordvec files
        print('---- Loading the processed GloVe files : ',end='')
        self.load_GloVe()
        print('Done')
        
        ########## TORCH EMBEDDING ##########
        
        # Defining variables for our Embedding:
        self.size_vocab = len(self.words)
        self.emb_matrix = torch.zeros((self.size_vocab,self.dim_vect))
        
        # Creating the Pytorch Embedding Layer : 
        print('---- Creating the Pytorch Embedding Layer  : ',end='')
        self.emb_layer = nn.Embedding(self.size_vocab, self.dim_vect)
        self.create_emb_layer(non_trainable=True)
        print('Done')

               
    def process_GloVe(self):
        ''' Processes the GloVe Dataset - Saves files'''
        words = []
        word2idx = {}
        
        vectors = bcolz.carray(np.zeros(1), rootdir=self.path_vec_save, mode='w') # defining vector saved

        idx = 0
        with open(self.path_vec_original, 'rb') as f:
            for l in f:
                line = l.decode().split()
                word = line[0]
                words.append(word)
                word2idx[word] = idx
                idx += 1
                vect = np.array(line[1:]).astype(np.float)
                vectors.append(vect)

        vectors = bcolz.carray(vectors[:].reshape((-1, self.dim_vect)), rootdir=self.path_vec_save, mode='w')

        vectors.flush()
        pickle.dump(words, open(self.path_words, 'wb'))
        pickle.dump(word2idx, open(self.path_word2idx, 'wb'))
        
    def load_GloVe(self):
        ''' Loads previously processed dataset'''
        
        vectors = bcolz.open(self.path_vec_save)[:]

        self.words = pickle.load(open(self.path_words, 'rb'))
        self.word2idx = pickle.load(open(self.path_word2idx, 'rb'))
        
        self.glove_dict = {w: vectors[self.word2idx[w]] for w in self.words}
        self.emb_matrix = torch.Tensor(vectors)
    
    def create_emb_layer(self, non_trainable=True):
        self.emb_layer.load_state_dict({'weight': self.emb_matrix})
        if non_trainable:
            self.emb_layer.weight.requires_grad = False


In [65]:
myEmbedding = GloVe_embedding(dim_vect=25)

---- Loading the processed GloVe files : Done
---- Creating the Pytorch Embedding Layer  : Done


## Data Loader
This Class Loads the Tweet Dataset, Cleans it. It also enables the loading for the training and testing. 
TODO : Loading for training and testing

In [209]:
class TestTweetDataset(Dataset):
    def __init__(self,data, subtask):
        data_  = data
        
        self.id = data_.index.tolist()
        self.token = data_.token.tolist()
        self.token_id = data_.token_id.tolist()
        
        
    def __getitem__(self, index):
        return self.id[index], torch.LongTensor(self.token_id[index])

    def __len__(self):
        return len(self.token) 
    
class TrainTweetDataset(Dataset):
    def __init__(self,data, subtask ):
        
          # Adapt to each subtask : 
        if subtask == 'subtask_a' :
            label_id_n = 'labelA'
            self.classes_dict = {'NOT' : 0 ,'OFF' : 1}
            data_ = data
            
        elif subtask == 'subtask_b' :
            label_id_n = 'labelB'
            self.classes_dict = {'UNT' : 0 ,'TIN' : 1}
            data_ = data.loc[(data['subtask_b'] == 'UNT') | (data['subtask_b'] == 'TIN') ]
            
        elif subtask == 'subtask_c' :
            label_id_n = 'labelC'
            self.classes_dict = {'IND' : 0 ,'OTH' : 1, 'GRP' : 2}
            data_ = data.loc[(data['subtask_c'] == 'IND') | (data['subtask_c'] == 'OTH') | (data['subtask_c'] == 'GRP') ]
            
        data_[label_id_n] = data_[subtask].apply(lambda x : self.classes_dict[x])  
        self.id = data_.index.tolist()
        self.label = data_[subtask].tolist()
        self.label_id = data_[label_id_n].tolist()
        self.token = data_.token.tolist()
        self.token_id = data_.token_id.tolist()
        
    def __getitem__(self, index):
        return self.label_id[index], torch.Tensor(self.token_id[index])

    def __len__(self):
        return len(self.token) 


    
class DataHandling(object):
    def __init__(self, embedding):
        
        self.embedding = embedding

        # All the Text Data path
        self.path = {}
        self.path_clean = {}
        
        self.path['train'] = join('..','data','start-kit','training-v1','offenseval-training-v1.tsv')
        self.path_clean['train'] = join('..','data','start-kit','training-v1','clean-offenseval-training-v1.tsv')
        
        self.path['subtask_a'] = join('..','data','Test A Release','testset-taska.tsv')
        self.path_clean['subtask_a'] = join('..','data','Test A Release','clean-testset-taska.tsv')
        
        self.path['subtask_b'] = join('..','data','Test B Release','testset-taskb.tsv')
        self.path_clean['subtask_b'] = join('..','data','Test B Release','clean-testset-taskb.tsv')
        
        self.path['subtask_c'] = join('..','data','Test C Release','test_set_taskc.tsv')
        self.path_clean['subtask_c'] = join('..','data','Test C Release','clean-test_set_taskc.tsv')
        
        self.data = {}
        
        if not(isfile(self.path_clean['train']) and isfile(self.path_clean['subtask_a']) and isfile(self.path_clean['subtask_b']) and isfile(self.path_clean['subtask_c']) ) : 
            ### PROCESSING OF THE ORIGINAL DATASET
            # Load, Clean and Tokenize the Datasets
            print('---- Load, Clean and Tokensize Dataset : ',end='')
            
            self.inital_dataload()
            print('Done')
            
            # Compute List of All words in the datasets
            print('---- Finalize tokenized words and translation to id : ',end='')
            self.all_words_freq = {}
            self.all_words = []
            self.compute_wordlist()
            self.token2id()
            print('Done')

            # Add Embedding and correct clean the words not in embedding : 
            print('---- Adapt Dataset for Embedding : ',end='')
            self.adaptDataset()
            print('Done')

            # Save the Cleaned Datasets
            print('---- Saving all tokenized words : ',end='')
            self.save_cleanDataset()
            print('Done')
        else : 
            # Save the Cleaned Datasets
            print('---- Load the Clean Adapted Dataset : ',end='')
            self.load_cleanDataset()
            print('Done')
            
            # Compute List of All words in the datasets
            print('---- Compute word list : ',end='')
            self.all_words_freq = {}
            self.all_words = []
            self.compute_wordlist()
            print('Done')
        
    def getDataset(self, dataT='train',subtask='subtask_a'):
        ''' Returns the pytorch Dataset
            - file : {'train','test'}
            - subtask : {'subtask_a','subtask_b','subtask_c'} '''
        
        if dataT == 'train':
            dataset = TrainTweetDataset(self.data[dataT], subtask)
        elif dataT == 'test':
            dataset = TestTweetDataset(self.data[subtask], subtask)
            
        return dataset
    
    def token2id(self):
        for f in self.path : 
            def token2id_x(x):
                
                return [self.embedding.word2idx[k] for k in x if k in self.embedding.words]
            self.data[f]['token_id'] = self.data[f]['token'].apply(lambda x : token2id_x(x))
            #print(self.data[f])

    def save_cleanDataset(self):
        for f in self.path : 
            self.data[f].to_csv(self.path_clean[f])
        
    def load_cleanDataset(self):
        for f in self.path : 
            self.data[f] = pd.read_csv(self.path_clean[f],index_col='id')
            self.data[f]['token'] = self.data[f]['token'].apply(lambda x : ast.literal_eval(x))
            self.data[f]['token_id'] = self.data[f]['token_id'].apply(lambda x : ast.literal_eval(x))
           
               
    def adaptDataset(self):
        # Find all words wich are not in the Embedding :
        missing_words = []
        for i, word in enumerate(self.all_words) :
            if self.embedding.word2idx.get(word) == None : 
                missing_words.append(word)
        
        # Correct if possible the missing_words : 
        ### We use theshold over which we correct the word. Under which we discard the word
        t = 0.5 # threshold
        rejected_words = []
        corrected_words = {}
        for word in tqdm(missing_words) : 
            suggestion, prob = spelling.suggest(word)[0]
            if prob < t : 
                rejected_words.append(word)
            else : 
                corrected_words[word] = suggestion
        
        # Modify the Original Datasets with those corrected_words : 
        for f in self.path : 
            self.data[f]['token'] = self.data[f]['token'].apply(lambda x : [corrected_words.get(k,k) for k in x])
            self.data[f]['token'] = self.data[f]['token'].apply(lambda x : [k for k in x if k not in rejected_words ])
        nb_rejected = len(rejected_words)
        nb_corrected = len(corrected_words)
        nb_vocab = len(self.embedding.glove_dict)
        p_rejected = 100* nb_rejected / nb_vocab
        p_corrected = 100* nb_corrected / nb_vocab
        print('---- Words removed   : {0:} / {1:.2f} - {2:} %'.format(nb_rejected,nb_vocab,p_rejected))
        print('---- Words corrected : {0:} / {1:.2f} - {2:} %'.format(nb_corrected,nb_vocab,p_corrected))
        
    def inital_dataload(self):
        for f in self.path : 
            self.data[f] = pd.read_table(self.path[f],index_col='id')
            self.data[f]['token'] = self.data[f]['tweet'].apply(lambda x : self.clean_tweet(x))
            
    def compute_wordlist(self):
        
        for f in self.data : 
            for i in range(len(self.data[f])):
                for e in self.data[f].iloc[i].token:
                    self.all_words_freq[e] = 1 + self.all_words_freq.get(e,0)
        self.all_words = list(self.all_words_freq.keys())
    
    def clean_tweet(self,text):
        ''' Function that is applied to every to tweet in the dataset '''
        
        # =========== TEXT ===========
        # Replace @USER by <user>
        text = re.compile(r'@USER').sub(r'<user>',text)

        # Replace URL by <url>
        text = re.compile(r'URL').sub(r'<url>',text)

        # Remove numbers :
        text = re.compile(r'[0-9]+').sub(r' ',text)

        # Remove some special characters
        text = re.compile(r'([\xa0_\{\}\[\]¬•$,:;/@#|\^*%().~`”"“-])').sub(r' ',text) 

        # Space the special characters with white spaces
        text = re.compile(r'([$&+,:;=?@#|\'.^*()%!"’“-])').sub(r' \1 ',text)
        
        # Replace some special characters : 
        replace_dict = {r'&' : 'and' , 
                        r'\+' : 'plus'}
        for cha in replace_dict:
            text = re.compile(str(cha)).sub(str(replace_dict[cha]),text)
            
        # Handle Emoji : translate some and delete the others
        text = self.handle_emoji(text)
        
        # Word delengthening : 
        text = re.compile(r'(.)\1{3,}').sub(r'\1\1',text)

        # Cut the words with caps in them : 
        text = re.compile(r'([a-z]+|[A-Z]+|[A-Z][a-z]+)([A-Z][a-z]+)').sub(r'\1 \2',text)
        text = re.compile(r'([a-z]+|[A-Z]+|[A-Z][a-z]+)([A-Z][a-z]+)').sub(r'\1 \2',text)        
        # =========== TOKENS ===========
        # TOKENIZE 
        text = text.split(' ')

        # Remove white spaces tokens
        text = [text[i] for i in range(len(text)) if text[i] != ' ']

        # Remove empty tokens
        text = [text[i] for i in range(len(text)) if text[i] != '']

        # Remove repetition in tokens (!!! => !)
        text = [text[i] for i in range(len(text)) if text[i] != text[i-1]]

        #  Handle the ALL CAPS Tweets 
        ### if ratio of caps in the word > 75% add allcaps tag <allcaps>
        caps_r = np.mean([text[i].isupper() for i in range(len(text))])
        if caps_r > 0.6 : 
            text.append('<allcaps>')

        # Lower Case : 
        text = [text[i].lower() for i in range(len(text))]

        return text

    def handle_emoji(self,text):
        # Dictionnary of "important" emojis : 
        emoji_dict =  {'♥️': ' love ',
                       '❤️' : ' love ',
                       '❤' : ' love ',
                       '😘' : ' kisses ',
                      '😭' : ' cry ',
                      '💪' : ' strong ',
                      '🌍' : ' earth ',
                      '💰' : ' money ',
                      '👍' : ' ok ',
                       '👌' : ' ok ',
                      '😡' : ' angry ',
                      '🍆' : ' dick ',
                      '🤣' : ' haha ',
                      '😂' : ' haha ',
                      '🖕' : ' fuck you '}

        for cha in emoji_dict:
            text = re.compile(str(cha)).sub(str(emoji_dict[cha]),text)
        # Remove ALL emojis
        text = emoji.get_emoji_regexp().sub(r' ',text) 
        text = re.compile("([\U0001f3fb-\U0001f3ff])").sub(r'',text) 
        text = re.compile("([\U00010000-\U0010ffff])").sub(r'',text) 
        text = re.compile("(\u00a9|\u00ae|[\u2000-\u3300]|\ud83c[\ud000-\udfff]|\ud83d[\ud000-\udfff]|\ud83e[\ud000-\udfff])").sub(r'',text)

        # Add Space between  the Emoji Expressions : 
        text = re.compile("([\U00010000-\U0010ffff])").sub(r' \1 ',text) 
        return text

In [185]:
mydata = DataHandling(myEmbedding)

---- Load the Clean Adapted Dataset : Done
---- Compute word list : Done


In [186]:
train = mydata.getDataset(dataT='train',subtask='subtask_c')
train[1]

/Users/adrian/anaconda3/envs/ic_std/lib/python3.6/site-packages/ipykernel/__main__.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


(1,
 tensor([0.0000e+00, 3.0167e+04, 7.0000e+01, 7.5000e+01, 6.6623e+05, 9.0000e+00]))

In [169]:
words = np.array(list(mydata.all_words_freq.keys()))
list(words[list(np.argsort(list(mydata.all_words_freq.values())))[:50]])

['tmi',
 'stairway',
 'winded',
 'wiccan',
 'shortsighted',
 'teleports',
 'doilies',
 'crocheting',
 'beatin',
 'glitchy',
 'brutally',
 'distrust',
 'synch',
 'commuted',
 'bojan',
 'konk',
 'appointee',
 'vocalist',
 'composer',
 'gillibrand',
 'carey',
 'personified',
 'sisterhood',
 'abs',
 'tulip',
 'slaughtering',
 'kardashian',
 'connelly',
 'whiney',
 'gavel',
 'quad',
 'usb',
 'token',
 'vary',
 'hells',
 'replays',
 'satanic',
 'omar',
 'brah',
 'cider',
 'carelessly',
 'apparantly',
 'indifference',
 'msn',
 'birdbrain',
 'serling',
 'neoliberal',
 'tee',
 'birdie',
 'normalizing']

In [170]:
mydata.data['train'].head(10)


tweet subtask_a subtask_b  \
id                                                                             
86426  @USER She should ask a few native Americans wh...       OFF       UNT   
90194  @USER @USER Go home you’re drunk!!! @USER #MAG...       OFF       TIN   
16820  Amazon is investigating Chinese employees who ...       NOT       NaN   
62688  @USER Someone should'veTaken" this piece of sh...       OFF       UNT   
43605  @USER @USER Obama wanted liberals &amp; illega...       NOT       NaN   
97670                  @USER Liberals are all Kookoo !!!       OFF       TIN   
77444                   @USER @USER Oh noes! Tough shit.       OFF       UNT   
52415  @USER was literally just talking about this lo...       OFF       TIN   
45157                         @USER Buy more icecream!!!       NOT       NaN   
13384  @USER Canada doesn’t need another CUCK! We alr...       OFF       TIN   

      subtask_c                                              token  \
id                                                                   
86426       NaN  [<user>, she, should, ask, a, few, native, ame...   
90194       IND  [<user>, go, home, you, re, drunk, !, <user>, ...   
16820       NaN  [amazon, is, investigating, chinese, employees...   
62688       NaN  [<user>, someone, should, ', ve, taken, this, ...   
43605       NaN  [<user>, obama, wanted, liberals, and, amp, il...   
97670       OTH            [<user>, liberals, are, all, kookoo, !]   
77444       NaN                 [<user>, oh, noes, !, tough, shit]   
52415       GRP  [<user>, was, literally, just, talking, about,...   
45157       NaN                   [<user>, buy, more, icecream, !]   
13384       IND  [<user>, canada, doesn, t, need, another, cuck...   

                                                token_id  
id                                                        
86426  [0, 147, 276, 564, 11, 1086, 17410, 7436, 86, ...  
90194  [0, 111, 335, 15, 796, 1510, 9, 0, 29895, 2862...  
16820  [2546, 32, 39458, 3491, 16269, 127, 70, 5441, ...  
62688  [0, 238, 276, 48, 571, 1941, 53, 2478, 39, 185...  
43605  [0, 1381, 952, 30167, 26, 12800, 114749, 16, 9...  
97670                      [0, 30167, 70, 75, 666232, 9]  
77444                      [0, 193, 73879, 9, 3831, 185]  
52415  [0, 93, 1468, 59, 653, 121, 53, 88, 75, 6865, ...  
45157                            [0, 872, 145, 18657, 9]  
13384  [0, 3159, 69392, 187, 171, 598, 407869, 9, 80,...

## Classifier 
Set of Classes used as classifier for the tweets. 

In [171]:
# Classification NN : 
class FFNN(nn.Module):
    
    def __init__(self, embedding, hidden_dim , num_classes ,embedding_dim):
        print('---- Creating FFNN : ',end='')
        
        super(FFNN, self).__init__()
        
        # Embedding
        self.embedding = embedding
        
        # Fully Connected Layers
        self.fc1 = nn.Linear(embedding_dim, hidden_dim)
        self.fc2 = nn.Linear(hidden_dim, num_classes) 
        
        # Activation Layers
        self.relu1 = nn.ReLU()
        self.output = nn.Sigmoid()
        print('Done')
    
    def forward(self, x):
        
        embedded = self.embedding(x)
        
        # we average the embeddings of words in a sentence
        averaged = embedded.mean(1)
        
        # (batch size, max sent length, embedding dim) to (batch size, embedding dim)

        out = self.fc1(averaged)
        out = self.relu1(out)
        out = self.fc2(out)
        out = self.output(out)
        return out


In [ ]:
class TweetDataLoader(DataLoader):
    def __init__(self,*args, **kwargs):
        super().__init__(*args, **kwargs)
        super()
    

## Main Class : Trainer
Main Class for the loading, training, testing etc ...

In [242]:
class OffensiveClassifier(object):
    ''' Main Class for the loading, training, testing etc ...'''
    def __init__(self,subtask='subtask_a', dim_vect=25,cType='FFNN'):
        
        self.dim_vect = dim_vect
        
        self.subtask = subtask

        # Loading the GloVe Embedding and Torch Formating of this Embedding
        self.GloVe = GloVe_embedding(dim_vect=dim_vect)
        self.embedding = self.GloVe.emb_layer
        
        # Loading the Tweet Data : 
        self.dataHandler = DataHandling(self.GloVe)
        
        # Retrieving Training DataSet (pytorch)
        self.train_set = self.dataHandler.getDataset('train',subtask)
        self.train_generator = DataLoader(self.train_set, batch_size=1 )
        
        # Retrieving Test DataSet (pytorch)
        self.test_set = self.dataHandler.getDataset('test',subtask)
        self.test_generator = DataLoader(self.test_set)
        
        # Classification : 
        if cType == 'FFNN':
            # Creating the Neuronal Network
            self.model = FFNN(self.embedding, 10, 1,self.dim_vect)
        if cType == 'logistic':
            pass
        

    def accuracy(self, output, target ):

        output = torch.round(torch.sigmoid(output))
        correct = (output == target).float()
        acc = correct.sum()/len(correct)
        return acc
    
    def train( self, nb_epochs ):

        # recall input parameters to our model
        #embedding_dim, hidden_dim, vocab_size, max_len, num_classes
        # max_len is the maximum length of the input sentences as we defined during padding

        # we use the stochastic gradient descent (SGD) optimizer
        optimizer = optim.SGD(self.model.parameters(),lr=0.1)
        
        loss_fn = nn.BCELoss()

        for epoch in range(nb_epochs):
            for target, tokens  in self.train_generator :
                target = target.float()
                tokens = tokens.long()
                #to ensure the dropout (exlained later) is "turned on" while training
                #good practice to include even if do not use here
                self.model.train()

                #we zero the gradients as they are not removed automatically
                optimizer.zero_grad()

                # queeze is needed as the predictions are initially size (batch size, 1) and we need to remove the dimension of size 1 
                predictions = self.model(tokens).squeeze(1)
                loss = loss_fn(predictions, target)
                acc = self.accuracy(predictions, target)
                
                #calculate the gradient of each parameter
                loss.backward()
                #update the parameters using the gradients and optimizer algorithm 
                optimizer.step()

                epoch_loss = loss.item()
                epoch_acc = acc

                print(f'| Epoch: {epoch:02} | Train Loss: {epoch_loss:.3f} | Train Acc: {epoch_acc*100:.2f}%')
                #print(f'| Epoch: {epoch:02} | Train Loss: {epoch_loss:.3f}')




In [243]:
taskAclassifier = OffensiveClassifier(subtask='subtask_a', dim_vect=25, cType='FFNN')

---- Loading the processed GloVe files : Done
---- Creating the Pytorch Embedding Layer  : Done
---- Load the Clean Adapted Dataset : Done
---- Compute word list : Done
---- Creating FFNN : Done


In [244]:
taskAclassifier.train(5)

| Epoch: 00 | Train Loss: 0.854 | Train Acc: 100.00%
| Epoch: 00 | Train Loss: 0.818 | Train Acc: 100.00%
| Epoch: 00 | Train Loss: 0.610 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.812 | Train Acc: 100.00%
| Epoch: 00 | Train Loss: 0.615 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.805 | Train Acc: 100.00%
| Epoch: 00 | Train Loss: 0.773 | Train Acc: 100.00%
| Epoch: 00 | Train Loss: 0.743 | Train Acc: 100.00%
| Epoch: 00 | Train Loss: 0.673 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.741 | Train Acc: 100.00%
| Epoch: 00 | Train Loss: 0.674 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.649 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.766 | Train Acc: 100.00%
| Epoch: 00 | Train Loss: 0.652 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.628 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.605 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.584 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.564 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.544 | Train Acc: 0.00%
| Epoch: 00 | T

| Epoch: 00 | Train Loss: 0.402 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 1.128 | Train Acc: 100.00%
| Epoch: 00 | Train Loss: 1.081 | Train Acc: 100.00%
| Epoch: 00 | Train Loss: 0.438 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.425 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.413 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.401 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.390 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 1.152 | Train Acc: 100.00%
| Epoch: 00 | Train Loss: 0.402 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.391 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.381 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.370 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 1.195 | Train Acc: 100.00%
| Epoch: 00 | Train Loss: 0.383 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.373 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.363 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.353 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.344 | Train Acc: 0.00%
| Epoch: 00 | Train Los

| Epoch: 00 | Train Loss: 0.462 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.448 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.435 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 1.065 | Train Acc: 100.00%
| Epoch: 00 | Train Loss: 1.022 | Train Acc: 100.00%
| Epoch: 00 | Train Loss: 0.470 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.456 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 1.029 | Train Acc: 100.00%
| Epoch: 00 | Train Loss: 0.987 | Train Acc: 100.00%
| Epoch: 00 | Train Loss: 0.948 | Train Acc: 100.00%
| Epoch: 00 | Train Loss: 0.910 | Train Acc: 100.00%
| Epoch: 00 | Train Loss: 0.540 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.522 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.506 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.948 | Train Acc: 100.00%
| Epoch: 00 | Train Loss: 0.514 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.935 | Train Acc: 100.00%
| Epoch: 00 | Train Loss: 0.523 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.506 | Train Acc: 0.00%
| Epoch: 00 | T

| Epoch: 00 | Train Loss: 1.042 | Train Acc: 100.00%
| Epoch: 00 | Train Loss: 1.000 | Train Acc: 100.00%
| Epoch: 00 | Train Loss: 0.483 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.984 | Train Acc: 100.00%
| Epoch: 00 | Train Loss: 0.492 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.969 | Train Acc: 100.00%
| Epoch: 00 | Train Loss: 0.931 | Train Acc: 100.00%
| Epoch: 00 | Train Loss: 0.894 | Train Acc: 100.00%
| Epoch: 00 | Train Loss: 0.550 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.884 | Train Acc: 100.00%
| Epoch: 00 | Train Loss: 0.557 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.539 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.522 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.506 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.948 | Train Acc: 100.00%
| Epoch: 00 | Train Loss: 0.514 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.936 | Train Acc: 100.00%
| Epoch: 00 | Train Loss: 0.523 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.923 | Train Acc: 100.00%
| Epoch: 00

| Epoch: 00 | Train Loss: 0.935 | Train Acc: 100.00%
| Epoch: 00 | Train Loss: 0.523 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.507 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.491 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.476 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.994 | Train Acc: 100.00%
| Epoch: 00 | Train Loss: 0.486 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.979 | Train Acc: 100.00%
| Epoch: 00 | Train Loss: 0.495 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.480 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.988 | Train Acc: 100.00%
| Epoch: 00 | Train Loss: 0.489 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.973 | Train Acc: 100.00%
| Epoch: 00 | Train Loss: 0.499 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.483 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.469 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 0.455 | Train Acc: 0.00%
| Epoch: 00 | Train Loss: 1.030 | Train Acc: 100.00%
| Epoch: 00 | Train Loss: 0.465 | Train Acc: 0.00%
| Epoch: 00 | Train

...

| Epoch: 04 | Train Loss: 0.314 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.307 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 1.351 | Train Acc: 100.00%
| Epoch: 04 | Train Loss: 0.320 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.312 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.305 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 1.355 | Train Acc: 100.00%
| Epoch: 04 | Train Loss: 0.318 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 1.321 | Train Acc: 100.00%
| Epoch: 04 | Train Loss: 0.331 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.323 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.315 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 1.328 | Train Acc: 100.00%
| Epoch: 04 | Train Loss: 0.328 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.320 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 1.314 | Train Acc: 100.00%
| Epoch: 04 | Train Loss: 0.333 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.325 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.317 | Train Acc: 0.00%
| Epoch: 04 | Train L

| Epoch: 04 | Train Loss: 0.466 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.453 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.440 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 1.057 | Train Acc: 100.00%
| Epoch: 04 | Train Loss: 0.450 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 1.038 | Train Acc: 100.00%
| Epoch: 04 | Train Loss: 0.997 | Train Acc: 100.00%
| Epoch: 04 | Train Loss: 0.484 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.470 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.456 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.443 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.430 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.418 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.406 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 1.119 | Train Acc: 100.00%
| Epoch: 04 | Train Loss: 0.418 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.406 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 1.119 | Train Acc: 100.00%
| Epoch: 04 | Train Loss: 0.418 | Train Acc: 0.00%
| Epoch: 04 | Train L

| Epoch: 04 | Train Loss: 0.354 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.345 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.337 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.328 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.321 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.313 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.306 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.299 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 1.372 | Train Acc: 100.00%
| Epoch: 04 | Train Loss: 0.312 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.305 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.298 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 1.375 | Train Acc: 100.00%
| Epoch: 04 | Train Loss: 0.311 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.304 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.297 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.291 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.284 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.278 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 1

| Epoch: 04 | Train Loss: 0.561 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.543 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.894 | Train Acc: 100.00%
| Epoch: 04 | Train Loss: 0.550 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.885 | Train Acc: 100.00%
| Epoch: 04 | Train Loss: 0.557 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.875 | Train Acc: 100.00%
| Epoch: 04 | Train Loss: 0.564 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.546 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.891 | Train Acc: 100.00%
| Epoch: 04 | Train Loss: 0.553 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.881 | Train Acc: 100.00%
| Epoch: 04 | Train Loss: 0.560 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.872 | Train Acc: 100.00%
| Epoch: 04 | Train Loss: 0.566 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.863 | Train Acc: 100.00%
| Epoch: 04 | Train Loss: 0.573 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.554 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.880 | Train Acc: 100.00%
| Epoch: 04 | T

| Epoch: 04 | Train Loss: 0.445 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 1.048 | Train Acc: 100.00%
| Epoch: 04 | Train Loss: 0.455 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.442 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.429 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.417 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 1.098 | Train Acc: 100.00%
| Epoch: 04 | Train Loss: 0.429 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.417 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.405 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.394 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.384 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 1.166 | Train Acc: 100.00%
| Epoch: 04 | Train Loss: 0.396 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.385 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.375 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 1.184 | Train Acc: 100.00%
| Epoch: 04 | Train Loss: 0.387 | Train Acc: 0.00%
| Epoch: 04 | Train Loss: 0.377 | Train Acc: 0.00%
| Epoch: 04 | Train Los

In [214]:
taskAclassifier.train_set[10]

(0,
 tensor([   0.,   33.,  137.,   78.,   29., 4157.,   15., 1215., 2797., 2031.]))

In [216]:
torch.LongTensor([   0.,   33.,  137.,   78.,   29., 4157.,   15., 1215., 2797., 2031.])

tensor([   0,   33,  137,   78,   29, 4157,   15, 1215, 2797, 2031])

In [247]:
dir(DataLoader)

['_DataLoader__initialized',
 '__class__',
 '__delattr__',
 '__dict__',
 '__dir__',
 '__doc__',
 '__eq__',
 '__format__',
 '__ge__',
 '__getattribute__',
 '__gt__',
 '__hash__',
 '__init__',
 '__init_subclass__',
 '__iter__',
 '__le__',
 '__len__',
 '__lt__',
 '__module__',
 '__ne__',
 '__new__',
 '__reduce__',
 '__reduce_ex__',
 '__repr__',
 '__setattr__',
 '__sizeof__',
 '__str__',
 '__subclasshook__',
 '__weakref__']